In [130]:
import sqlite3
import os
import pandas as pd

# 预测价格数据
dbfilename = os.path.join(r'D:\code\PriceForecast\yuanyoudataset','jbsh_yuanyou.db')
conn = sqlite3.connect(dbfilename)
query = 'SELECT * FROM accuracy'
df1 = pd.read_sql_query(query, conn)
df1['ds'] =  df1['PREDICT_DATE']
conn.close()
print(df1.shape)




# 最高最低价
xlsfilename = os.path.join(r'D:\code\PriceForecast\yuanyoudataset','数据项下载.xls')
df2 = pd.read_excel(xlsfilename)[5:]
df2 = df2.rename(columns = {'数据项名称':'ds','布伦特最低价':'LOW_PRICE','布伦特最高价':'HIGH_PRICE'})
print(df2.shape)



df = pd.merge(df1,df2,on=['ds'],how='left')

df['ds'] =  pd.to_datetime(df['ds'])
df['PREDICT_DATE'] =  pd.to_datetime(df['PREDICT_DATE'])
df = df.reindex()

print(df.shape)

df.to_csv(os.path.join(r'D:\code\PriceForecast\yuanyoudataset','123.csv'))
# df = df[['ds','min_within_quantile','max_within_quantile']]



# 打印数据框的前几行
print(df.head())
print(df.tail())


(50, 9)
(20, 4)
(50, 12)
   id PREDICT_DATE  CREAT_DATE  MIN_PRICE  MAX_PRICE HIGH_PRICE_x LOW_PRICE_x  \
0   1   2024-11-26  2024-11-25  71.071556  76.006900                            
1   2   2024-11-27  2024-11-25  71.003624  75.580560                            
2   3   2024-11-28  2024-11-25  72.083850  76.204260                            
3   4   2024-11-29  2024-11-25  71.329730  75.703950                            
4   5   2024-12-02  2024-11-25  71.720825  76.264275                            

  RIGHT_ROTE         ds   序号 LOW_PRICE_y HIGH_PRICE_y  
0            2024-11-26  9.0       71.63        73.80  
1            2024-11-27  8.0       71.71        72.85  
2            2024-11-28  7.0       71.85        72.96  
3            2024-11-29  6.0       71.75        73.34  
4            2024-12-02  5.0       71.52        72.89  
    id PREDICT_DATE  CREAT_DATE  MIN_PRICE  MAX_PRICE HIGH_PRICE_x  \
45  46   2024-12-09  2024-12-06  68.894770  73.909450                
46  47   202

In [131]:
# 定义一个函数来计算准确率
def calculate_accuracy(row):
    if row['HIGH_PRICE_y'] > row['MIN_PRICE']:
        sorted_prices = sorted([row['LOW_PRICE_y'], row['MIN_PRICE'], row['MAX_PRICE'], row['HIGH_PRICE_y']])
        middle_diff = sorted_prices[2] - sorted_prices[1]
        price_range = row['HIGH_PRICE_y'] - row['LOW_PRICE_y']
        accuracy = middle_diff / price_range
        return accuracy
    else:
        return 0

# 使用 apply 函数来应用计算准确率的函数

columns = ['HIGH_PRICE_y','LOW_PRICE_y','MIN_PRICE','MAX_PRICE']
df[columns] = df[columns].astype(float)
df['ACCURACY'] = df.apply(calculate_accuracy, axis=1)


# 打印结果
print(df[['ds','ACCURACY',]+columns])

df = df[['ds','ACCURACY','PREDICT_DATE','CREAT_DATE']+columns]

           ds  ACCURACY  HIGH_PRICE_y  LOW_PRICE_y  MIN_PRICE  MAX_PRICE
0  2024-11-26  1.000000         73.80        71.63  71.071556  76.006900
1  2024-11-27  1.000000         72.85        71.71  71.003624  75.580560
2  2024-11-28  0.789324         72.96        71.85  72.083850  76.204260
3  2024-11-29  1.000000         73.34        71.75  71.329730  75.703950
4  2024-12-02  0.853412         72.89        71.52  71.720825  76.264275
5  2024-11-27  0.606873         72.85        71.71  72.158165  76.173650
6  2024-11-28  0.802144         72.96        71.85  72.069620  76.447000
7  2024-11-29  0.608239         73.34        71.75  72.372900  76.082910
8  2024-12-02  0.457007         72.89        71.52  72.263900  76.198685
9  2024-12-03  0.758302         73.93        71.68  72.223820  76.041725
10 2024-11-28  1.000000         72.96        71.85  70.709750  75.208030
11 2024-11-29  1.000000         73.34        71.75  69.923110  75.423775
12 2024-12-02  1.000000         72.89        71.52 

In [132]:
import datetime
# ds 按周取
df['Ds_Week'] = df['ds'].apply(lambda x: x.strftime('%U'))
df['Pre_Week'] = df['PREDICT_DATE'].apply(lambda x: x.strftime('%U'))

In [133]:
df

ds  ACCURACY PREDICT_DATE  CREAT_DATE  HIGH_PRICE_y  LOW_PRICE_y  \
0  2024-11-26  1.000000   2024-11-26  2024-11-25         73.80        71.63   
1  2024-11-27  1.000000   2024-11-27  2024-11-25         72.85        71.71   
2  2024-11-28  0.789324   2024-11-28  2024-11-25         72.96        71.85   
3  2024-11-29  1.000000   2024-11-29  2024-11-25         73.34        71.75   
4  2024-12-02  0.853412   2024-12-02  2024-11-25         72.89        71.52   
5  2024-11-27  0.606873   2024-11-27  2024-11-26         72.85        71.71   
6  2024-11-28  0.802144   2024-11-28  2024-11-26         72.96        71.85   
7  2024-11-29  0.608239   2024-11-29  2024-11-26         73.34        71.75   
8  2024-12-02  0.457007   2024-12-02  2024-11-26         72.89        71.52   
9  2024-12-03  0.758302   2024-12-03  2024-11-26         73.93        71.68   
10 2024-11-28  1.000000   2024-11-28  2024-11-27         72.96        71.85   
11 2024-11-29  1.000000   2024-11-29  2024-11-27         73.34        71.75   
12 2024-12-02  1.000000   2024-12-02  2024-11-27         72.89        71.52   
13 2024-12-03  1.000000   2024-12-03  2024-11-27         73.93        71.68   
14 2024-12-04  1.000000   2024-12-04  2024-11-27         74.28        72.25   
15 2024-11-29  1.000000   2024-11-29  2024-11-28         73.34        71.75   
16 2024-12-02  1.000000   2024-12-02  2024-11-28         72.89        71.52   
17 2024-12-03  1.000000   2024-12-03  2024-11-28         73.93        71.68   
18 2024-12-04  1.000000   2024-12-04  2024-11-28         74.28        72.25   
19 2024-12-05  1.000000   2024-12-05  2024-11-28         72.92        71.80   
20 2024-12-02  0.000000   2024-12-02  2024-11-29         72.89        71.52   
21 2024-12-03  0.000000   2024-12-03  2024-11-29         73.93        71.68   
22 2024-12-04  0.000000   2024-12-04  2024-11-29         74.28        72.25   
23 2024-12-05  0.000000   2024-12-05  2024-11-29         72.92        71.80   
24 2024-12-06  0.000000   2024-12-06  2024-11-29         72.19        70.85   
25 2024-12-03  1.000000   2024-12-03  2024-12-02         73.93        71.68   
26 2024-12-04  1.000000   2024-12-04  2024-12-02         74.28        72.25   
27 2024-12-05  1.000000   2024-12-05  2024-12-02         72.92        71.80   
28 2024-12-06  1.000000   2024-12-06  2024-12-02         72.19        70.85   
29 2024-12-09  0.000000   2024-12-09  2024-12-02           NaN          NaN   
30 2024-12-04  0.943207   2024-12-04  2024-12-03         74.28        72.25   
31 2024-12-05  0.643920   2024-12-05  2024-12-03         72.92        71.80   
32 2024-12-06  0.040172   2024-12-06  2024-12-03         72.19        70.85   
33 2024-12-09  0.000000   2024-12-09  2024-12-03           NaN          NaN   
34 2024-12-10  0.000000   2024-12-10  2024-12-03           NaN          NaN   
35 2024-12-05  0.000000   2024-12-05  2024-12-04         72.92        71.80   
36 2024-12-06  0.000000   2024-12-06  2024-12-04         72.19        70.85   
37 2024-12-09  0.000000   2024-12-09  2024-12-04           NaN          NaN   
38 2024-12-10  0.000000   2024-12-10  2024-12-04           NaN          NaN   
39 2024-12-11  0.000000   2024-12-11  2024-12-04           NaN          NaN   
40 2024-12-06  0.000000   2024-12-06  2024-12-05         72.19        70.85   
41 2024-12-09  0.000000   2024-12-09  2024-12-05           NaN          NaN   
42 2024-12-10  0.000000   2024-12-10  2024-12-05           NaN          NaN   
43 2024-12-11  0.000000   2024-12-11  2024-12-05           NaN          NaN   
44 2024-12-12  0.000000   2024-12-12  2024-12-05           NaN          NaN   
45 2024-12-09  0.000000   2024-12-09  2024-12-06           NaN          NaN   
46 2024-12-10  0.000000   2024-12-10  2024-12-06           NaN          NaN   
47 2024-12-11  0.000000   2024-12-11  2024-12-06           NaN          NaN   
48 2024-12-12  0.000000   2024-12-12  2024-12-06           NaN          NaN   
49 2024-12-13  0.000000   2024-12-13  2024-12-06           Na

In [134]:
# 取结束日期上一周的日期
endtime = '2024-12-9'
endtimeweek = datetime.datetime.strptime(endtime, '%Y-%m-%d')
up_week = endtimeweek - datetime.timedelta(days=endtimeweek.weekday() + 14)
up_week_dates = [up_week + datetime.timedelta(days=i) for i in range(14)][4:-2]
up_week_dates = [date.strftime('%Y-%m-%d') for date in up_week_dates]
print(up_week_dates)


df3 = df.copy()
df3 = df3[df3['CREAT_DATE'].isin(up_week_dates)]
df3 = df3[df3['PREDICT_DATE'].isin(up_week_dates)]
print(df3.shape)
df3.to_csv('up_week_dates.csv',index=False)

['2024-11-29', '2024-11-30', '2024-12-01', '2024-12-02', '2024-12-03', '2024-12-04', '2024-12-05', '2024-12-06']
(15, 10)


In [135]:
total = len(df3)
accuracy_rote = 0
# for i,group in df3.groupby('CREAT_DATE'):
for i,group in df3.groupby('ds'):
    print(i)
    print('权重：',round(len(group)/total,2))
    print('准确率：',group['ACCURACY'].sum()/(len(group)/total))
    accuracy_rote += group['ACCURACY'].sum()/(len(group)/total)

print(accuracy_rote)

2024-12-02 00:00:00
权重： 0.07
准确率： 0.0
2024-12-03 00:00:00
权重： 0.13
准确率： 7.5
2024-12-04 00:00:00
权重： 0.2
准确率： 9.716034482758616
2024-12-05 00:00:00
权重： 0.27
准确率： 6.1646986607143
2024-12-06 00:00:00
权重： 0.33
准确率： 3.1205149253731137
26.50124806884603
